In [3]:
import numpy as np
import pickle
class BlackJack:
    
    def __init__(self, lr=0.08, exp_rate=0.25):
        self.player_Q_Values = {}  
        # Start Q-Table |
        for i in range(12, 22):
            for j in range(1, 12):
                for k in [True, False]:
                    self.player_Q_Values[(i, j)] = {}
                    for a in [1, 0]:
                        self.player_Q_Values[(i, j)][a] = 0
        
        self.player_state_action = []
        self.state = (0, 0)  # Initial First state
        self.actions = [1, 0]  # 1: Hit  0: Stick
        self.end = False
        self.lr = lr
        self.exp_rate = exp_rate
    
    
    @staticmethod
    def draw_black():
        # Draw uniformly from the black deck
        # Calling this function in the first round
        black_deck = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
        return int(np.random.choice(black_deck))
    
    @staticmethod
    def draw_card():
        # Callin this method every following round
        if np.random.rand() < 0.25:
            # Subtrack value with 25%
            red_deck = [-1, -2, -3 , -4, -5, -6, -7, -8, -9, -10]
            return int(np.random.choice(red_deck))
        else:
            # Add value with 75%
            black_deck = [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]
            return int(np.random.choice(black_deck))
       
            
    def dealerPolicy(self, current_value, is_end):
        if current_value > 21:
            return current_value, True
        # If above 16 -> dealer stops taking cards
        if current_value >= 16:
            return current_value, True
        else:
            card = self.draw_card()
            return current_value+card, False        
               
            
    def chooseAction(self):
        current_value = self.state[0]
        if current_value <= 11:
            return 1
        
        elif np.random.uniform(0, 1) <= self.exp_rate:
            action = np.random.choice(self.actions)
        else:
            v = -np.inf
            action = 0            
            for a in self.player_Q_Values[self.state]:
                if self.player_Q_Values[self.state][a] > v:
                    action = a
                    v = self.player_Q_Values[self.state][a]
        return action
    
    
    def PlayerNextState(self, action):
        current_value = self.state[0]
        show_card = self.state[1]
        
        if current_value > 21:
            self.end = True
            self.state = (current_value, show_card) # End Turn
            return 
        
        if action:
            card = self.draw_card()
            current_value += card
        else:
            self.end = True
        # If getting above 21 in the round
        if current_value > 21:
            self.end = True
        self.state = (current_value, show_card)
    
    def _KeepScore(self, player_value, dealer_value, is_end=True):
        reward = 0
        if is_end:
            if player_value > 21:
                if dealer_value > 21:
                    reward = 0
                    print('Both over 21 - Draw')
                else:
                    reward = -1
                    print('Dealer won the round')
            else:
                if dealer_value > 21:
                    reward = 1
                    print('Player won the round')
                else:
                    if player_value < dealer_value:
                        reward = -1
                        print('Dealer won the round')
                    elif player_value > dealer_value:
                        reward = 1
                        print('Player won the round')
                    else:
                        reward = 0
                        print('Draw')
                        
        # Backpropagate each Reward
        for s in reversed(self.player_state_action):
            state, action = s[0], s[1]
            reward = self.lr*(reward - self.player_Q_Values[state][action])
            self.player_Q_Values[state][action] += reward
            
    def reset(self):
        self.player_state_action = []
        self.state = (0, 0)  # initial state
        self.end = False
    
    def play(self, rounds=1000):
        wins = np.zeros(2)
        for i in range(rounds):
            if i % 1000 == 0:
                print("round", i)
                
            # Giving out two cards each (21 can't be reached with 10 as max number)
            dealer_value, player_value = 0, 0
            show_card = 0
            
            # Player receives 2 cards, first black
            
            card = self.draw_black()
            player_value += card
            self.state = (player_value, show_card)
            
            card = self.draw_card()
            player_value += card
            self.state = (player_value, show_card)

            # Dealer receives 2 cards, first black
        
            card = self.draw_black()
            show_card = card
            dealer_value += card
            
            self.state = (player_value, show_card)
            card = self.draw_card()
            dealer_value += card
            
            # Play the game until a player sticks   
            while True:
                action = self.chooseAction()
                if self.state[0] >= 12:
                    self.player_state_action.append([self.state, action])
                # Update player's next state
                self.PlayerNextState(action)
                if self.end:
                    break    

            # Dealer's turn
            is_end = False
            while not is_end:
                dealer_value, is_end = self.dealerPolicy(dealer_value, is_end)

            # Detail Winner
            # Rewards + update Q values
            player_value = self.state[0]
            print("Player value {} | dealer value {}".format(player_value, dealer_value))
            self._KeepScore(player_value, dealer_value)
            self.reset()
        print(wins)
    
    # Saving the policy
    def savePolicy(self, file="policy"):
        fw = open(file, 'wb')
        pickle.dump(self.player_Q_Values, fw)
        fw.close()

    def loadPolicy(self, file="policy"):
        fr = open(file,'rb')
        self.player_Q_Values = pickle.load(fr)
        fr.close()
        
    # Training with Dealer
    def playWithDealer(self, rounds=1000):
        self.reset()
        self.loadPolicy()
        self.exp_rate = 0
        
        result = np.zeros(3)  # Player [win, draw, lose]
        for _ in range(rounds):
            # Give out two cards at the Start
            dealer_value, player_value = 0, 0
            show_card = 0

            # First card black and then 75% black and 25% red 
            card = self.draw_black()
            show_card = card
            dealer_value += card
            self.state = (player_value, show_card)
            # card 2
            card = self.draw_card()
            dealer_value += card
            
            # Player's turn
            # Player gets 2 cards
            card = self.draw_black()
            player_value += card
            self.state = (player_value, show_card)
            
            card = self.draw_card()
            player_value += card
            self.state = (player_value, show_card)
            
            # Player's turn
            while True:
                action = self.chooseAction()
                # Update each net State
                self.PlayerNextState(action)
                if self.end:
                    break    
            # Dealer's turn
            is_end = False
            while not is_end:
                dealer_value, is_end = self.dealerPolicy(dealer_value, is_end)
            # Track Score
            player_value = self.state[0]

            if player_value > 21:
                if dealer_value > 21:
                    # Draw
                    result[1] += 1
                else:
                    result[2] += 1
            else:
                if dealer_value > 21:
                    result[0] += 1
                else:
                    if player_value < dealer_value:
                        result[2] += 1
                    elif player_value > dealer_value:
                        result[0] += 1
                    else:
                        # draw
                        result[1] += 1
            self.reset()
        return result

In [4]:
b = BlackJack()
b.play(100000)

round 0
Player value 24 | dealer value 18
Dealer won the round
Player value 20 | dealer value 16
Player won the round
Player value 12 | dealer value 17
Dealer won the round
Player value 28 | dealer value 19
Dealer won the round
Player value 26 | dealer value 21
Dealer won the round
Player value 13 | dealer value 18
Dealer won the round
Player value 23 | dealer value 16
Dealer won the round
Player value 25 | dealer value 20
Dealer won the round
Player value 12 | dealer value 21
Dealer won the round
Player value 23 | dealer value 22
Both over 21 - Draw
Player value 24 | dealer value 24
Both over 21 - Draw
Player value 30 | dealer value 24
Both over 21 - Draw
Player value 20 | dealer value 23
Player won the round
Player value 25 | dealer value 17
Dealer won the round
Player value 27 | dealer value 16
Dealer won the round
Player value 22 | dealer value 16
Dealer won the round
Player value 14 | dealer value 16
Dealer won the round
Player value 12 | dealer value 19
Dealer won the round
Playe

Player value 17 | dealer value 16
Player won the round
Player value 18 | dealer value 18
Draw
Player value 20 | dealer value 18
Player won the round
Player value 21 | dealer value 18
Player won the round
Player value 18 | dealer value 17
Player won the round
Player value 23 | dealer value 17
Dealer won the round
Player value 18 | dealer value 22
Player won the round
round 1000
Player value 26 | dealer value 16
Dealer won the round
Player value 17 | dealer value 22
Player won the round
Player value 20 | dealer value 18
Player won the round
Player value 22 | dealer value 23
Both over 21 - Draw
Player value 23 | dealer value 17
Dealer won the round
Player value 19 | dealer value 22
Player won the round
Player value 16 | dealer value 17
Dealer won the round
Player value 25 | dealer value 21
Dealer won the round
Player value 18 | dealer value 18
Draw
Player value 22 | dealer value 18
Dealer won the round
Player value 21 | dealer value 16
Player won the round
Player value 21 | dealer value 1

Player value 16 | dealer value 22
Player won the round
Player value 19 | dealer value 16
Player won the round
Player value 23 | dealer value 19
Dealer won the round
Player value 17 | dealer value 20
Dealer won the round
Player value 22 | dealer value 19
Dealer won the round
Player value 20 | dealer value 18
Player won the round
Player value 12 | dealer value 18
Dealer won the round
Player value 19 | dealer value 17
Player won the round
Player value 23 | dealer value 18
Dealer won the round
Player value 16 | dealer value 17
Dealer won the round
Player value 18 | dealer value 17
Player won the round
Player value 22 | dealer value 22
Both over 21 - Draw
Player value 21 | dealer value 17
Player won the round
Player value 22 | dealer value 17
Dealer won the round
Player value 23 | dealer value 18
Dealer won the round
Player value 17 | dealer value 21
Dealer won the round
Player value 22 | dealer value 19
Dealer won the round
Player value 19 | dealer value 23
Player won the round
Player valu

Dealer won the round
Player value 16 | dealer value 21
Dealer won the round
Player value 20 | dealer value 22
Player won the round
Player value 18 | dealer value 22
Player won the round
Player value 19 | dealer value 19
Draw
Player value 20 | dealer value 21
Dealer won the round
Player value 26 | dealer value 18
Dealer won the round
Player value 20 | dealer value 22
Player won the round
Player value 20 | dealer value 18
Player won the round
Player value 25 | dealer value 17
Dealer won the round
Player value 17 | dealer value 21
Dealer won the round
Player value 20 | dealer value 16
Player won the round
Player value 12 | dealer value 17
Dealer won the round
Player value 18 | dealer value 20
Dealer won the round
Player value 17 | dealer value 19
Dealer won the round
Player value 15 | dealer value 18
Dealer won the round
Player value 15 | dealer value 19
Dealer won the round
Player value 19 | dealer value 21
Dealer won the round
Player value 18 | dealer value 23
Player won the round
Playe

Draw
Player value 19 | dealer value 20
Dealer won the round
Player value 19 | dealer value 20
Dealer won the round
Player value 18 | dealer value 19
Dealer won the round
Player value 23 | dealer value 23
Both over 21 - Draw
Player value 24 | dealer value 22
Both over 21 - Draw
Player value 17 | dealer value 21
Dealer won the round
Player value 18 | dealer value 18
Draw
Player value 22 | dealer value 16
Dealer won the round
Player value 18 | dealer value 16
Player won the round
Player value 23 | dealer value 24
Both over 21 - Draw
Player value 20 | dealer value 18
Player won the round
Player value 17 | dealer value 18
Dealer won the round
Player value 26 | dealer value 18
Dealer won the round
Player value 22 | dealer value 17
Dealer won the round
Player value 19 | dealer value 17
Player won the round
Player value 18 | dealer value 16
Player won the round
Player value 14 | dealer value 25
Player won the round
Player value 18 | dealer value 22
Player won the round
Player value 18 | dealer

...

Player won the round
Player value 17 | dealer value 22
Player won the round
Player value 22 | dealer value 18
Dealer won the round
Player value 18 | dealer value 25
Player won the round
Player value 22 | dealer value 16
Dealer won the round
Player value 24 | dealer value 18
Dealer won the round
Player value 17 | dealer value 17
Draw
Player value 20 | dealer value 18
Player won the round
Player value 18 | dealer value 23
Player won the round
Player value 24 | dealer value 21
Dealer won the round
Player value 17 | dealer value 21
Dealer won the round
Player value 20 | dealer value 17
Player won the round
Player value 22 | dealer value 16
Dealer won the round
Player value 17 | dealer value 23
Player won the round
Player value 17 | dealer value 20
Dealer won the round
Player value 17 | dealer value 20
Dealer won the round
Player value 17 | dealer value 21
Dealer won the round
Player value 15 | dealer value 16
Dealer won the round
Player value 21 | dealer value 16
Player won the round
Playe

Player value 22 | dealer value 23
Both over 21 - Draw
Player value 16 | dealer value 17
Dealer won the round
Player value 21 | dealer value 21
Draw
Player value 24 | dealer value 19
Dealer won the round
Player value 23 | dealer value 16
Dealer won the round
Player value 24 | dealer value 20
Dealer won the round
Player value 19 | dealer value 20
Dealer won the round
Player value 18 | dealer value 17
Player won the round
Player value 16 | dealer value 16
Draw
Player value 25 | dealer value 19
Dealer won the round
Player value 20 | dealer value 17
Player won the round
Player value 14 | dealer value 16
Dealer won the round
Player value 20 | dealer value 25
Player won the round
Player value 18 | dealer value 16
Player won the round
Player value 18 | dealer value 19
Dealer won the round
Player value 22 | dealer value 22
Both over 21 - Draw
Player value 22 | dealer value 16
Dealer won the round
Player value 20 | dealer value 20
Draw
Player value 17 | dealer value 17
Draw
Player value 18 | dea

Both over 21 - Draw
Player value 19 | dealer value 17
Player won the round
Player value 19 | dealer value 17
Player won the round
Player value 20 | dealer value 16
Player won the round
Player value 19 | dealer value 23
Player won the round
Player value 23 | dealer value 23
Both over 21 - Draw
Player value 14 | dealer value 19
Dealer won the round
Player value 21 | dealer value 24
Player won the round
Player value 13 | dealer value 16
Dealer won the round
Player value 21 | dealer value 19
Player won the round
Player value 17 | dealer value 20
Dealer won the round
Player value 18 | dealer value 23
Player won the round
Player value 21 | dealer value 19
Player won the round
Player value 24 | dealer value 16
Dealer won the round
Player value 21 | dealer value 18
Player won the round
Player value 21 | dealer value 18
Player won the round
Player value 23 | dealer value 18
Dealer won the round
Player value 19 | dealer value 18
Player won the round
Player value 12 | dealer value 19
Dealer won t

Player value 21 | dealer value 16
Player won the round
Player value 19 | dealer value 16
Player won the round
Player value 21 | dealer value 16
Player won the round
Player value 20 | dealer value 22
Player won the round
Player value 18 | dealer value 16
Player won the round
Player value 23 | dealer value 16
Dealer won the round
Player value 20 | dealer value 18
Player won the round
Player value 21 | dealer value 24
Player won the round
Player value 16 | dealer value 21
Dealer won the round
Player value 20 | dealer value 16
Player won the round
Player value 21 | dealer value 20
Player won the round
Player value 23 | dealer value 16
Dealer won the round
Player value 20 | dealer value 17
Player won the round
Player value 20 | dealer value 16
Player won the round
Player value 22 | dealer value 16
Dealer won the round
Player value 23 | dealer value 19
Dealer won the round
Player value 19 | dealer value 18
Player won the round
Player value 14 | dealer value 18
Dealer won the round
Player val

Player value 14 | dealer value 21
Dealer won the round
Player value 20 | dealer value 16
Player won the round
Player value 20 | dealer value 16
Player won the round
Player value 23 | dealer value 20
Dealer won the round
Player value 19 | dealer value 16
Player won the round
Player value 17 | dealer value 20
Dealer won the round
Player value 12 | dealer value 18
Dealer won the round
Player value 24 | dealer value 17
Dealer won the round
Player value 16 | dealer value 17
Dealer won the round
Player value 22 | dealer value 17
Dealer won the round
Player value 23 | dealer value 16
Dealer won the round
Player value 12 | dealer value 19
Dealer won the round
Player value 17 | dealer value 21
Dealer won the round
Player value 21 | dealer value 16
Player won the round
Player value 22 | dealer value 22
Both over 21 - Draw
Player value 23 | dealer value 21
Dealer won the round
Player value 23 | dealer value 17
Dealer won the round
Player value 20 | dealer value 22
Player won the round
Player valu

In [5]:
b.savePolicy()

In [6]:
games = b.playWithDealer(rounds=10000)
games

array([4458., 1477., 4065.])